> **Exercise:** Bots Discovery
>
> In the dataset `ratings_bots.csv`, some users may be bots. To help a movie sucess they add ratings (favorable ones often). To get a better recommendation, we try to remove them.
>
> * Count the users with a mean rating above 4.7/5 and delete them 
>
>   *hint:* the [nunique](https://pandas.pydata.org/pandas-docs/stable/generated/pandas.DataFrame.nunique.html)  function may be helpful to count
>
>
> * Delete multiples reviews of a movie by a single user by replacing them with only the first one. What is the proportion of potential bots among the users?
>
>   *hint:* the `groupby` function can be applied to several columns, also `reset_index(drop=True)` removes the grouby indexing. 
>
>  *hint:* remember the `loc` function, e.g.  `df.loc[df['userId'] == 128]` returns a dataframe of the rows where the userId is 128; and `df.loc[df['userId'] == 128].loc[samerev['movieId'] == 3825]` returns a dataframe of the rows where the userId is 128 **and** the movieID is 3825.
>
>  In total , 17 ratings have to be removed. For instance, user 128 has 3 ratings of the movie 3825
>
> This dataset has around 100 000 ratings so hand picking won't do!




In [1]:
import pandas as pd
import numpy as np

ratings_bots = pd.read_csv('data/ml-small/ratings_bots.csv')

In [2]:
def meanCheck(x):
    return x["rating"].mean() <= 4.7

def meanCheckInv(x):
    return x["rating"].mean() > 4.7


filtered = ratings_bots.groupby("userId").filter(meanCheck)
to_remove = ratings_bots.groupby("userId").filter(meanCheckInv)

tot = ratings_bots["userId"].nunique()
nonBots = filtered["userId"].nunique()

print("Total users: {:4d} \t\t Too nice ratings: {:4d}".format(tot,tot-nonBots))

Total users:  671 		 Too nice ratings:    5


In [3]:
to_remove.groupby("userId")["rating"].describe()

count      mean       std  min  25%  50%  75%  max
userId                                                    
46       39.0  4.948718  0.191767  4.0  5.0  5.0  5.0  5.0
298      75.0  4.800000  0.486299  3.0  5.0  5.0  5.0  5.0
443      40.0  4.850000  0.324235  3.5  5.0  5.0  5.0  5.0
448      20.0  4.750000  0.638666  3.0  5.0  5.0  5.0  5.0
622      31.0  4.725806  0.693286  2.0  5.0  5.0  5.0  5.0

In [4]:
to_remove

userId  movieId  rating   timestamp
7298       46       73     5.0  1366389910
7299       46      355     5.0  1366392410
7300       46      724     5.0  1366389683
7301       46     1270     5.0  1366392989
7302       46     1359     4.5  1366389877
...       ...      ...     ...         ...
93442     622    99114     4.5  1424225358
93443     622   100553     5.0  1424225101
93444     622   108979     3.5  1424225074
93445     622   109487     5.0  1424225001
93446     622   112852     5.0  1424225012

[205 rows x 4 columns]

In [5]:
def removeMultiple(x):
    if x["rating"].count()>1:
        base = np.array(x["rating"])
        user = np.array(x["userId"])[0]
        movie = np.array(x["movieId"])[0]
        print("Multiple entries: user {:6d}     movie {:6d}    number of multiples {:3d}".format(user,movie,len(base)))
        x = x.drop(x.index[1:])
        x["rating"].iloc[0] = base.mean()
        x["potential bots"] = [True]
    return x
        

samerev = filtered.groupby(["userId","movieId"]).apply(removeMultiple).reset_index(drop=True)

Multiple entries: user    128     movie   3825    number of multiples   3
Multiple entries: user    264     movie   1097    number of multiples   9
Multiple entries: user    427     movie    919    number of multiples   7
Multiple entries: user    671     movie   5816    number of multiples   2


In [6]:
samerev.head()

userId  movieId  rating   timestamp potential bots
0       1       31     2.5  1260759144            NaN
1       1     1029     3.0  1260759179            NaN
2       1     1061     3.0  1260759182            NaN
3       1     1129     2.0  1260759185            NaN
4       1     1172     4.0  1260759205            NaN

In [7]:
def fillBot(x):
    if x["potential bots"].sum()>=1:
        x = x.fillna(True)
    else:
        x = x.fillna(False)
    return x
    

final = samerev.groupby(["userId"]).apply(fillBot).reset_index(drop=True)

In [8]:
final.head()

userId  movieId  rating   timestamp  potential bots
0       1       31     2.5  1260759144           False
1       1     1029     3.0  1260759179           False
2       1     1061     3.0  1260759182           False
3       1     1129     2.0  1260759185           False
4       1     1172     4.0  1260759205           False

In [9]:
final.groupby("potential bots")["userId"].nunique()

potential bots
False    662
True       4
Name: userId, dtype: int64

In [10]:
def select_bots(x):
    return x["potential bots"].any() ==True

final.groupby("userId").filter(select_bots ).groupby("userId")['rating'].count()

userId
128    323
264     33
427    294
671    115
Name: rating, dtype: int64

<div class="exo"> **Exercise 3.2.2:** Planets discovery <br/><br/>

We will use the Planets dataset, available via the [Seaborn package](http://seaborn.pydata.org/) (see further). It provides information on how astronomers found new planets around stars, *exoplanets*.


<ul>
<li>Diplay median, mean and quantile informations for these planets orbital periods, masses, and distances.</li>
<li>For each method, display statistic on the years planets were discovered using this technique.</li>
<li>Display a table giving the number of planets discovered by each methods in each decade (1980s to 2010s)<br/>
* **hint:** the decade can be obtained as series with <tt>10 (planets['year'] // 10)</tt> and this series can be used in a groupby operation on the dataframe even though it is not a column.*</li>
</ul>

</div>

In [11]:
import pandas as pd
import numpy as np

planets = pd.read_csv('data/planets.csv')
print(planets.shape)
planets.head()

(1035, 6)


method  number  orbital_period   mass  distance  year
0  Radial Velocity       1         269.300   7.10     77.40  2006
1  Radial Velocity       1         874.774   2.21     56.95  2008
2  Radial Velocity       1         763.000   2.60     19.84  2011
3  Radial Velocity       1         326.030  19.40    110.62  2007
4  Radial Velocity       1         516.220  10.50    119.47  2009

In [12]:
planets[["mass","distance","orbital_period"]].describe()

mass     distance  orbital_period
count  513.000000   808.000000      992.000000
mean     2.638161   264.069282     2002.917596
std      3.818617   733.116493    26014.728304
min      0.003600     1.350000        0.090706
25%      0.229000    32.560000        5.442540
50%      1.260000    55.250000       39.979500
75%      3.040000   178.500000      526.005000
max     25.000000  8500.000000   730000.000000

In [13]:
planets.groupby('method')['year'].describe()

count         mean       std     min      25%  \
method                                                                         
Astrometry                       2.0  2011.500000  2.121320  2010.0  2010.75   
Eclipse Timing Variations        9.0  2010.000000  1.414214  2008.0  2009.00   
Imaging                         38.0  2009.131579  2.781901  2004.0  2008.00   
Microlensing                    23.0  2009.782609  2.859697  2004.0  2008.00   
Orbital Brightness Modulation    3.0  2011.666667  1.154701  2011.0  2011.00   
Pulsar Timing                    5.0  1998.400000  8.384510  1992.0  1992.00   
Pulsation Timing Variations      1.0  2007.000000       NaN  2007.0  2007.00   
Radial Velocity                553.0  2007.518987  4.249052  1989.0  2005.00   
Transit                        397.0  2011.236776  2.077867  2002.0  2010.00   
Transit Timing Variations        4.0  2012.500000  1.290994  2011.0  2011.75   

                                  50%      75%     max  
method                                                  
Astrometry                     2011.5  2012.25  2013.0  
Eclipse Timing Variations      2010.0  2011.00  2012.0  
Imaging                        2009.0  2011.00  2013.0  
Microlensing                   2010.0  2012.00  2013.0  
Orbital Brightness Modulation  2011.0  2012.00  2013.0  
Pulsar Timing                  1994.0  2003.00  2011.0  
Pulsation Timing Variations    2007.0  2007.00  2007.0  
Radial Velocity                2009.0  2011.00  2014.0  
Transit                        2012.0  2013.00  2014.0  
Transit Timing Variations      2012.5  2013.25  2014.0

In [14]:
decade = 10 * (planets['year'] // 10)
decade = decade.astype(str) + 's'
decade.name = 'decade'
planets.groupby(['method', decade])['number'].sum().unstack().fillna(0).astype(int)

decade                         1980s  1990s  2000s  2010s
method                                                   
Astrometry                         0      0      0      2
Eclipse Timing Variations          0      0      5     10
Imaging                            0      0     29     21
Microlensing                       0      0     12     15
Orbital Brightness Modulation      0      0      0      5
Pulsar Timing                      0      9      1      1
Pulsation Timing Variations        0      0      1      0
Radial Velocity                    1     52    475    424
Transit                            0      0     64    712
Transit Timing Variations          0      0      0      9